In [71]:
# run from .demilunes pyenv 
import ee
import geemap
import os
ee.Authenticate()
ee.Initialize()


Enter verification code:  4/1AfgeXvv9zmyIbolkXUuHqxEtD689wSa3xLNnzpRDcqGL56J8ZT15AbxGi5o



Successfully saved authorization token.


In [ ]:
def gee_DEM_Slope(UNQ_num, aoi_shape, out_folder):
    # export the ImageCollection locally
    gdf = gpd.read_file(aoi_shape)
    gdf = gdf[gdf.UNQ == int(UNQ_num)]
    gdf_web = gdf.to_crs("EPSG:4326")
    geom = ee.Geometry.Rectangle([gdf_web.bounds.minx.min(), gdf_web.bounds.miny.min(), gdf_web.bounds.maxx.max(), gdf_web.bounds.maxy.max()])

    ele = ee.Image("NASA/NASADEM_HGT/001").select(['elevation'])
    dem = ee.Image(ele.resample('bilinear').reproject(crs='EPSG:32632', scale=10).clip(geom))
    slope = ee.Image(ee.Terrain.slope(ele).resample('bilinear').reproject(crs='EPSG:32632', scale=10).clip(geom))

    out_dir_full = os.path.join(out_folder, str(UNQ_num).zfill(3))
    if not os.path.exists(out_dir_full):
        os.makedirs(out_dir_full)
    dem_name=os.path.join(out_dir_full, "NASA_DEM_UNQ"+str(UNQ_num).zfill(3)+".tif")
    slope_name=os.path.join(out_dir_full, "NASA_Slope_UNQ"+str(UNQ_num).zfill(3)+".tif")


    geemap.ee_export_image(dem, dem_name,
                           region=geom, scale=10, crs='EPSG:32632', file_per_band=True)
    geemap.ee_export_image(slope, slope_name,
                           region=geom, scale=10, crs='EPSG:32632', file_per_band=True)

In [ ]:
aoi_shape="/home/sandbox-cel/DL/vector/AOIs/NigerGrid_RCT2_UTM32.gpkg"
out_folder="/home/sandbox-cel/DL/raster/grids/22_23/"
for UNQ_num in sorted(os.listdir(out_folder)):
    gee_DEM_Slope(UNQ_num, aoi_shape, out_folder)

In [ ]:
## MAKE TOPOGRPAHIC VARS

grid_dir="/home/sandbox-cel/DL/raster/grids/22_23/"
grid_files = ["/home/sandbox-cel/DL/vector/AOIs/Niger_RCT2_grid_East.gpkg",  "/home/sandbox-cel/DL/vector/AOIs/Niger_RCT2_grid_West.gpkg",
              "/home/sandbox-cel/DL/vector/AOIs/Niger_RCT2_grid_South.gpkg", "/home/sandbox-cel/DL/vector/AOIs/Niger_RCT2_grid_North.gpkg"]
image_name_dict = {"USGS/SRTMGL1_003":"SRTM_"}
GEE_NAME="USGS/SRTMGL1_003"
for grid_file in grid_files:
    gdf = gpd.read_file(grid_file)
    gdf_web = gdf.to_crs('EPSG:4326')
    for k, cell in gdf_web.iterrows():
        aoi = ee.Geometry.Rectangle([cell.geometry.bounds[0], cell.geometry.bounds[1], cell.geometry.bounds[2], cell.geometry.bounds[3]])
        UNQ = int(cell['UNQ'])
        print(UNQ)
        full_outDir = os.path.join(grid_dir, str(UNQ).zfill(3))
        if not os.path.exists(full_outDir):
            pass
        else:
            if "SRTM" in GEE_NAME:
                DEM_img = ee.Image(GEE_NAME).select('elevation').clip(aoi).rename("DEM")
                DEM_img = DEM_img.resample('bilinear').reproject(crs="EPSG:32632", scale=10)
                projection = DEM_img.projection().getInfo()
                SLOPE_img = ee.Terrain.slope(DEM_img).clip(aoi).rename("SLOPE")
                # split downloading of AOI
                download_tiles = geemap.fishnet(aoi, rows=1, cols=1, delta=0)
                band="DEM"
                geemap.download_ee_image_tiles(image=DEM_img,  features=download_tiles,
                                               crs=projection.get('crs'), crs_transform=projection.get('transform'),
                                               scale=10,
                                               prefix=os.path.join(full_outDir, image_name_dict.get(GEE_NAME)+str(band)+"_UNQ"+str(UNQ).zfill(3)+"_" ) )

                band="SLOPE"
                geemap.download_ee_image_tiles(image=SLOPE_img,  features=download_tiles,
                                               crs=projection.get('crs'), crs_transform=projection.get('transform'),
                                               scale=10,
                                               prefix=os.path.join(full_outDir, image_name_dict.get(GEE_NAME)+str(band)+"_UNQ"+str(UNQ).zfill(3)+"_" ) )



In [ ]:
# Set the date range
start_date = '2017-01-01'
end_date = '2018-01-01'
# Set region as AOI bbox
region = ee.Geometry.BBox(8.1, 13.1,  8.7, 13.9)
Map = geemap.Map()
Map.add_basemap('HYBRID')
# Set the region of interest by simply drawing a polygon on the map
Map.centerObject(region)
# Create Dynamic World land cover composite
dw_class = geemap.dynamic_world(region, start_date, end_date, return_type='class')
landcover_hill = geemap.dynamic_world(region, start_date, end_date, return_type='hillshade')
# Add Dynamic World to map
dw_vis = {
    "min": 0,
    "max": 8,
    "palette": [
        "#419BDF",
        "#397D49",
        "#88B053",
        "#7A87C6",
        "#E49635",
        "#DFC35A",
        "#C4281B",
        "#A59B8F",
        "#B39FE1",
    ],
}
Map.addLayer(dw_class, dw_vis, 'DW Land Cover', False)
Map.addLayer(dw_hill, {}, 'DW Land Cover Hillshade')
#Add legend 
Map.add_legend(title="Dynamic World Land Cover", builtin_legend='Dynamic_World')
Map

In [ ]:
yr=start_date[:4]
out_dir = r"G:\Shared drives\demilunes\Data\01_Data_raw_and_preProcessed\DynamicWorld"
filename = out_dir + "\Dynamic_World_LC_" + str(yr) + ".tif"
image = dw_class.clip(region).unmask()
geemap.ee_export_image(
    image, filename=filename, scale=90, region=region, file_per_band=False
)